<a href="https://colab.research.google.com/github/Dasika-Vaishnavi/Twitter_virality_COMS_4705/blob/main/Finetuned_Roberta.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

1. Install and Import Required Libraries


In [ ]:
# Run in Colab only if needed:
!pip install datasets transformers torch tqdm

import pandas as pd
from datasets import load_dataset
from transformers import RobertaTokenizer, RobertaModel
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
import numpy as np
import random
from tqdm import tqdm


In [ ]:
SEED = 4705
torch.manual_seed(SEED)
np.random.seed(SEED)
random.seed(SEED)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(SEED)


In [ ]:
# Hugging Face dataset
dataset = load_dataset('siddharthgowda/twitter_500k_EN_only')
df = pd.DataFrame(dataset['train'])

# Engagement calculation
for col in ["replies", "retweets", "likes", "quotes"]:
    df[col] = pd.to_numeric(df[col], errors="coerce").fillna(0).astype(int)
df["engagement"] = df["replies"] + df["retweets"] + df["likes"] + df["quotes"]

# 5-label quantile binning
custom_quantiles = [0.0, 0.05, 0.30, 0.70, 0.95, 1.0]
custom_labels = [0, 1, 2, 3, 4]
df["labels"], bins = pd.qcut(
    df["engagement"].rank(method="first"),
    q=custom_quantiles,
    labels=custom_labels,
    retbins=True,
    duplicates="drop"
)

# Stratified sample (140k tweets)
SAMPLE_SIZE = 140_000
_, ds_sample_df, _, _ = train_test_split(
    df, df['labels'],
    test_size=min(SAMPLE_SIZE, len(df)),
    random_state=SEED,
    stratify=df['labels']
)


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/534 [00:00<?, ?B/s]

data/train-00000-of-00001.parquet:   0%|          | 0.00/88.1M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/574137 [00:00<?, ? examples/s]

In [ ]:
X = ds_sample_df['tweet'].values
y = ds_sample_df['labels'].values.astype(int)

X_temp, X_test, y_temp, y_test = train_test_split(
    X, y, test_size=0.1667, random_state=SEED, stratify=y
)
X_train, X_val, y_train, y_val = train_test_split(
    X_temp, y_temp, test_size=0.2, random_state=SEED, stratify=y_temp
)

train_df = pd.DataFrame({'text': X_train, 'labels': y_train})
val_df = pd.DataFrame({'text': X_val, 'labels': y_val})
test_df = pd.DataFrame({'text': X_test, 'labels': y_test})


In [ ]:
model_name = 'roberta-base'
tokenizer = RobertaTokenizer.from_pretrained(model_name)
max_length = 128

class TwitterDataset(Dataset):
    def __init__(self, df, tokenizer, max_length):
        self.texts = df['text'].tolist()
        self.labels = df['labels'].tolist()
        self.tokenizer = tokenizer
        self.max_length = max_length
    def __len__(self): return len(self.texts)
    def __getitem__(self, idx):
        encoding = self.tokenizer(
            str(self.texts[idx]),
            truncation=True, padding='max_length',
            max_length=self.max_length, return_tensors='pt'
        )
        item = {k: v.squeeze(0) for k, v in encoding.items()}
        item['labels'] = torch.tensor(int(self.labels[idx]), dtype=torch.long)
        return item

BATCH_SIZE = 8  # Small for resource efficiency
train_dataset = TwitterDataset(train_df, tokenizer, max_length)
val_dataset = TwitterDataset(val_df, tokenizer, max_length)
test_dataset = TwitterDataset(test_df, tokenizer, max_length)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=BATCH_SIZE)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE)


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/481 [00:00<?, ?B/s]

In [ ]:
class RobertaLayerNormClassifier(nn.Module):
    def __init__(self, model_name='roberta-base', num_labels=5):
        super().__init__()
        self.roberta = RobertaModel.from_pretrained(model_name)
        self.norm = nn.LayerNorm(self.roberta.config.hidden_size)
        self.classifier = nn.Linear(self.roberta.config.hidden_size, num_labels)
    def forward(self, input_ids, attention_mask):
        outputs = self.roberta(input_ids=input_ids, attention_mask=attention_mask)
        features = outputs.last_hidden_state[:, 0, :]
        normed_features = self.norm(features)
        logits = self.classifier(normed_features)
        return logits

model = RobertaLayerNormClassifier(num_labels=5)  # Number of classes is 5
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)


model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


RobertaLayerNormClassifier(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-11): 12 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (

In [ ]:
from torch.optim import AdamW
from torch.nn import CrossEntropyLoss

optimizer = AdamW(model.parameters(), lr=2e-5)
criterion = CrossEntropyLoss()

def train_epoch(model, loader, optimizer, criterion, device, log_interval=1):
    model.train()
    total_loss = 0
    correct, total = 0, 0
    for step, batch in enumerate(tqdm(loader, desc="Train")):
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)

        optimizer.zero_grad()
        outputs = model(input_ids, attention_mask)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()

        preds = torch.argmax(outputs, dim=1)
        correct += (preds == labels).sum().item()
        total += labels.size(0)
        acc = correct / total
        print(f"Step {step+1:>5} | Batch Loss: {loss.item():.4f} | Running Acc: {acc:.4f}")
    avg_loss = total_loss / len(loader)
    final_acc = correct / total
    return avg_loss, final_acc

def eval_epoch(model, loader, criterion, device):
    model.eval()
    total_loss, correct, total = 0, 0, 0
    for step, batch in enumerate(tqdm(loader, desc="Val")):
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)
        with torch.no_grad():
            outputs = model(input_ids, attention_mask)
            loss = criterion(outputs, labels)
            preds = torch.argmax(outputs, dim=1)
            correct += (preds == labels).sum().item()
            total += labels.size(0)
            total_loss += loss.item()
    accuracy = correct / total
    avg_loss = total_loss / len(loader)
    return avg_loss, accuracy

num_epochs = 3
for epoch in range(num_epochs):
    print(f"\nEpoch {epoch+1}/{num_epochs}")
    train_loss, train_acc = train_epoch(model, train_loader, optimizer, criterion, device, log_interval=1)
    val_loss, val_acc = eval_epoch(model, val_loader, criterion, device)
    print(f"Epoch {epoch+1} | Train Loss: {train_loss:.4f} | Train Acc: {train_acc:.4f} | Val Loss: {val_loss:.4f} | Val Acc: {val_acc:.4f}")



Epoch 1/3


Train:   0%|          | 3/11667 [00:01<1:18:38,  2.47it/s]

Step     1 | Batch Loss: 1.5767 | Running Acc: 0.2500
Step     2 | Batch Loss: 1.7838 | Running Acc: 0.1875
Step     3 | Batch Loss: 1.8434 | Running Acc: 0.2083


Train:   0%|          | 7/11667 [00:01<30:39,  6.34it/s]

Step     4 | Batch Loss: 1.6065 | Running Acc: 0.2188
Step     5 | Batch Loss: 1.1936 | Running Acc: 0.2750
Step     6 | Batch Loss: 1.4985 | Running Acc: 0.2708
Step     7 | Batch Loss: 1.3380 | Running Acc: 0.2857


...

Step 11664 | Batch Loss: 1.2803 | Running Acc: 0.5462


Train: 100%|██████████| 11667/11667 [10:37<00:00, 18.30it/s]


Step 11665 | Batch Loss: 1.3051 | Running Acc: 0.5461
Step 11666 | Batch Loss: 0.8736 | Running Acc: 0.5461
Step 11667 | Batch Loss: 2.8390 | Running Acc: 0.5461


Val: 100%|██████████| 2917/2917 [00:56<00:00, 51.76it/s]

Epoch 3 | Train Loss: 1.0902 | Train Acc: 0.5461 | Val Loss: 1.1502 | Val Acc: 0.5236


In [ ]:
import torch
from sklearn.metrics import accuracy_score, classification_report

def evaluate_model(model, test_loader, device):
    model.eval()
    all_preds = []
    all_labels = []
    with torch.no_grad():
        for batch in test_loader:
            # Move inputs to device
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['labels'].to(device)

            # Forward pass
            logits = model(input_ids, attention_mask)
            preds = torch.argmax(logits, dim=1)

            # Collect results
            all_preds.extend(preds.cpu().numpy())
            all_labels.extend(labels.cpu().numpy())

    acc = accuracy_score(all_labels, all_preds)
    report = classification_report(all_labels, all_preds)
    print(f'Accuracy: {acc:.4f}')
    print(f'Classification Report:\n{report}')

# Usage (after training):
evaluate_model(model, test_loader, device)


Accuracy: 0.5210
Classification Report:
              precision    recall  f1-score   support

           0       0.00      0.00      0.00      1167
           1       0.54      0.44      0.48      5835
           2       0.53      0.66      0.59      9335
           3       0.50      0.59      0.54      5834
           4       0.80      0.00      0.01      1167

    accuracy                           0.52     23338
   macro avg       0.47      0.34      0.32     23338
weighted avg       0.51      0.52      0.49     23338



/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [ ]:
sample_tweet = "This is a test tweet. Will it go viral?"
encoding = tokenizer(
    sample_tweet, truncation=True, padding='max_length',
    max_length=max_length, return_tensors='pt'
)
input_ids = encoding['input_ids'].to(device)
attention_mask = encoding['attention_mask'].to(device)
with torch.no_grad():
    logits = model(input_ids, attention_mask)
    predicted_class = torch.argmax(logits, dim=1).item()
print("Predicted virality label:", predicted_class)


Predicted virality label: 2


In [ ]:
# First, let's check what columns are actually in your test_df
print("Available columns in test_df:")
print(test_df.columns.tolist())
print("\nFirst few rows:")
print(test_df.head())


Available columns in test_df:
['text', 'labels']

First few rows:
                                                text  labels
0  @jenniferdoleac I don’t think we ever stopped ...       2
1  We pretty much knew what to do concerning a fl...       1
2  Thrilled to get the notification this morning ...       3
3  The #WebSummit women in tech community has spo...       3
4  When should content strategy enter the design ...       1


In [ ]:
# Test on 10 random real tweets from test set and cross-check with actual virality
import random
import pandas as pd

# Select 10 random samples from test set
random.seed(42)  # For reproducibility
random_indices = random.sample(range(len(test_df)), min(10, len(test_df)))
test_samples = test_df.iloc[random_indices].reset_index(drop=True)

# Define virality labels (adjust these based on your dataset's classification)
virality_labels = {
    0: 'Not Viral',
    1: 'Low Viral',
    2: 'Medium Viral',
    3: 'High Viral'
}

print("=" * 100)
print("TESTING 10 RANDOM REAL TWEETS - PREDICTION vs ACTUAL")
print("=" * 100)

results = []

for i, row in test_samples.iterrows():
    tweet_text = row['text']
    actual_label = row['labels']  # Changed from 'virality_label' to 'labels'

    # Tokenize and predict
    encoding = tokenizer(
        tweet_text,
        truncation=True,
        padding='max_length',
        max_length=max_length,
        return_tensors='pt'
    )
    input_ids = encoding['input_ids'].to(device)
    attention_mask = encoding['attention_mask'].to(device)

    with torch.no_grad():
        logits = model(input_ids, attention_mask)
        predicted_class = torch.argmax(logits, dim=1).item()

    # Store results
    match = predicted_class == actual_label
    results.append({
        'index': i,
        'actual': actual_label,
        'predicted': predicted_class,
        'match': match
    })

    # Display results
    print(f"\n{'─' * 100}")
    print(f"Tweet #{i+1}:")
    print(f"Text: {tweet_text[:150]}..." if len(tweet_text) > 150 else f"Text: {tweet_text}")
    print(f"\nActual Label: {actual_label} ({virality_labels.get(actual_label, 'Unknown')})")
    print(f"Predicted Label: {predicted_class} ({virality_labels.get(predicted_class, 'Unknown')})")

    # Check if prediction matches
    match_symbol = "✓ CORRECT" if match else "✗ WRONG"
    print(f"Result: {match_symbol}")

print(f"\n{'=' * 100}")

# Calculate accuracy on these 10 samples
correct = sum(1 for r in results if r['match'])
accuracy = correct / len(results) * 100 if len(results) > 0 else 0
print(f"Accuracy on these 10 random samples: {accuracy:.2f}% ({correct}/{len(results)})")
print("=" * 100)

# Show confusion details
print("\nSummary:")
for r in results:
    status = "✓" if r['match'] else "✗"
    print(f"  {status} Tweet {r['index']+1}: Actual={r['actual']} ({virality_labels.get(r['actual'], 'Unknown')}), Predicted={r['predicted']} ({virality_labels.get(r['predicted'], 'Unknown')})")


TESTING 10 RANDOM REAL TWEETS - PREDICTION vs ACTUAL

────────────────────────────────────────────────────────────────────────────────────────────────────
Tweet #1:
Text: Brandon Broderick Monthly Update http://t.co/cEJc0cBqE6

Actual Label: 0 (Not Viral)
Predicted Label: 1 (Low Viral)
Result: ✗ WRONG

────────────────────────────────────────────────────────────────────────────────────────────────────
Tweet #2:
Text: Un nuevo jefe Count Bass D

Actual Label: 1 (Low Viral)
Predicted Label: 1 (Low Viral)
Result: ✓ CORRECT

────────────────────────────────────────────────────────────────────────────────────────────────────
Tweet #3:
Text: Houston Astros WORLD SERIES Hype https://t.co/V9HSoQcLDB via @YouTube Game 1 tonight!! #TheAthleteStop will be cheering on the Astros! It’s #OurTime! ...

Actual Label: 1 (Low Viral)
Predicted Label: 1 (Low Viral)
Result: ✓ CORRECT

────────────────────────────────────────────────────────────────────────────────────────────────────
Tweet #4:
Text: #SCOTU

In [ ]:
RobertaModel
